In [12]:
import socket, struct
import time

In [13]:
MESSAGE_SIZE = 24  # each doubles 8 bytes + 1 byte for delimiter
# Message Length Prefix (comment out other options)
# MESSAGE_SIZE = 0  # Will be calculated dynamically
 
# Delimiter (comment out other options)
DELIMITER = b'\n'
 
TCP_IP = '156.62.80.83'
TCP_PORT = 50000
BUFFER_SIZE = MESSAGE_SIZE if MESSAGE_SIZE else 32  # Minimum for two doubles

In [14]:
def send_data(conn, val):
  """Sends two double-precision numbers."""
  # Fixed Size
  msg = struct.pack('>d', val)
  conn.send(msg)

def receive_data(conn):
    """Receives three double-precision numbers."""
    if MESSAGE_SIZE:
        data = conn.recv(MESSAGE_SIZE)
        val1, val2, Time = struct.unpack('>ddd', data)
    else:
        # Delimiter
        val1 = None
        val2 = None
        Time = None
        while True:
            data = conn.recv(BUFFER_SIZE)
            if DELIMITER in data:
                val1_bytes, remaining = data.split(DELIMITER, 1)
                val1 = struct.unpack('>d', val1_bytes)[0]
                if DELIMITER in remaining:
                    val2_bytes, time_bytes = remaining.split(DELIMITER, 1)
                    val2 = struct.unpack('>d', val2_bytes)[0]
                    Time = struct.unpack('>d', time_bytes)[0]
                    break
    return val1, val2, Time

In [18]:
# close connection if it is already open
try:
    conn.close()
except:
    pass

s = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
s.bind((TCP_IP, TCP_PORT))
print('Waiting for Simulink to start')
s.listen(1)
conn, addr = s.accept()
print('Connection address: ', addr)

Waiting for Simulink to start
Connection address:  ('156.62.80.83', 45056)


In [19]:
V_ref = 5
Kp = 0.0001
Ki = 0.01
dt = 1 / 100000
u = 0

while True:
    # Send data to Simulink
    send_data(conn, u)
    # print('Duty cycle is:', u)

    # Receive data from Simulink
    val1, val2, time = receive_data(conn)
    # print('Voltage is:', val2)
    # print('Current is:', val1)
    print('Time is:', time)

    e = V_ref - val2
    u = u + Kp * e + Ki * dt * e

conn.close()


Time is: 0.0
Time is: 1e-05
Time is: 2e-05
Time is: 3.0000000000000004e-05
Time is: 4e-05
Time is: 5e-05
Time is: 6.000000000000001e-05
Time is: 7.000000000000001e-05
Time is: 8e-05
Time is: 9e-05
Time is: 0.0001
Time is: 0.00011
Time is: 0.00012000000000000002
Time is: 0.00013000000000000002
Time is: 0.00014000000000000001
Time is: 0.00015000000000000001
Time is: 0.00016
Time is: 0.00017
Time is: 0.00018
Time is: 0.00019
Time is: 0.0002
Time is: 0.00021
Time is: 0.00022
Time is: 0.00023
Time is: 0.00024000000000000003
Time is: 0.00025
Time is: 0.00026000000000000003
Time is: 0.00027
Time is: 0.00028000000000000003
Time is: 0.00029
Time is: 0.00030000000000000003
Time is: 0.00031
Time is: 0.00032
Time is: 0.00033000000000000005
Time is: 0.00034
Time is: 0.00035000000000000005
Time is: 0.00036
Time is: 0.00037000000000000005
Time is: 0.00038
Time is: 0.00039000000000000005
Time is: 0.0004
Time is: 0.00041000000000000005
Time is: 0.00042
Time is: 0.00043000000000000004
Time is: 0.00044
T

KeyboardInterrupt: 